### Fetching The 7z archive

In [0]:
try:
    dbutils.fs.ls("file:/databricks/driver/dblp.v13.7z")
    print("Archive in filesystem (file:/databricks/driver/dblp.v13.7z)")
except:
    try:
        dbutils.fs.ls("dbfs:/FileStore/data/dblp.v13.7z")
        print("Archive located in FileStore. Copying into local store..")
        dbutils.fs.cp("dbfs:/FileStore/data/dblp.v13.7z", "file:/databricks/driver/dblp.v13.7z")
        print("Completed")
    except:
        print("7z archive not found. Fetching from URL...")
        !wget https://originalstatic.aminer.cn/misc/dblp.v13.7z
        print("7z archive Downloaded. Moving archive to FileStore..")
        dbutils.fs.mkdirs("dbfs:/FileStore/data")
        dbutils.fs.cp("file:/databricks/driver/dblp.v13.7z", "dbfs:/FileStore/data/dblp.v13.7z")
        print("Completed.")

Archive located in FileStore. Copying into local store..


In [0]:
dbutils.fs.ls("file:/databricks/driver/dblp.v13.7z")

Out[10]: [FileInfo(path='file:/databricks/driver/dblp.v13.7z', name='dblp.v13.7z', size=2568255035, modificationTime=1650451287248)]

### Extracting Archive into json

**Skip this Section if you already have performed the extraction process.**

#### 1. Extraction

In [0]:
!pip install py7zr -q

You should consider upgrading via the '/databricks/python3/bin/python -m pip install --upgrade pip' command.


In [0]:
import py7zr

archive = py7zr.SevenZipFile('dblp.v13.7z', mode='r')
archive.extractall()
archive.close()

In [0]:
dbutils.fs.ls("file:/databricks/driver/dblpv13.json")

Out[13]: [FileInfo(path='file:/databricks/driver/dblpv13.json', name='dblpv13.json', size=17352640799, modificationTime=1631240655155)]

#### 2. Cleaning NumberInt(#) tags

In [0]:
import re

# Cleaning the `NumberInt` tag
fin = open(f"dblpv13.json")
fout = open(f"dblpv13_clean.json", "wt")
for line in fin:
    fout.write(re.sub(r"NumberInt\([\d]*\)", lambda x: "".join(re.findall(r"\d", x.group(0))), line))
fin.close()
fout.close()

#### 3. Partitioning Dataset into JSON files

In [0]:
!pip install ijson tqdm -q

You should consider upgrading via the '/databricks/python3/bin/python -m pip install --upgrade pip' command.


In [0]:
%mkdir data

In [0]:
import ijson
import json
from tqdm import tqdm
import decimal

class DecimalEncoder(json.JSONEncoder):
    def default(self, o):
        if isinstance(o, decimal.Decimal):
            return str(o)
        return super(DecimalEncoder, self).default(o)

data_dir = 'data/'
with open('dblpv13_clean.json', 'r') as f:
    counter, file_id = 0, 0
    file_buffer = []
    for obj_data in ijson.items(f, 'item'):
        file_buffer.append(obj_data)
        counter += 1
        if counter % 300000 == 0:
            print(f" Saving, data_PART_{file_id}.json in {data_dir}")
            f = open(f'{data_dir}data_PART_{file_id}.json', 'w')
            dump = json.dumps(file_buffer, cls=DecimalEncoder)
            f.write(dump)
            f.close()
            file_id += 1
            file_buffer = []
f = open(f'{data_dir}data_PART_{file_id}.json', 'w')
dump = json.dumps(file_buffer, cls=DecimalEncoder)
print(f" Saving, data_PART_{file_id}.json in {data_dir}")
f.write(dump)
f.close()
file_id += 1
file_buffer = []

 Saving, data_PART_0.json in data/
 Saving, data_PART_1.json in data/
 Saving, data_PART_2.json in data/
 Saving, data_PART_3.json in data/
 Saving, data_PART_4.json in data/
 Saving, data_PART_5.json in data/
 Saving, data_PART_6.json in data/
 Saving, data_PART_7.json in data/
 Saving, data_PART_8.json in data/
 Saving, data_PART_9.json in data/
 Saving, data_PART_10.json in data/
 Saving, data_PART_11.json in data/
 Saving, data_PART_12.json in data/
 Saving, data_PART_13.json in data/
 Saving, data_PART_14.json in data/
 Saving, data_PART_15.json in data/
 Saving, data_PART_16.json in data/
 Saving, data_PART_17.json in data/


#### 4. Moving files to dbfs FileStore from instance storage, to make it available for later.

In [0]:
# removing old json stored in filestore.
dbutils.fs.rm("dbfs:/FileStore/data/split_data/", recurse = True)
# Creating dir to store json in filestore..
dbutils.fs.mkdirs("dbfs:/FileStore/data/split_data")
# confirming dir is empty
dbutils.fs.ls("dbfs:/FileStore/data/split_data")

Out[34]: []

In [0]:
# Copying all json parts into filestore.
dbutils.fs.cp("file:/databricks/driver/data/", "dbfs:/FileStore/data/split_data", recurse = True)

Out[35]: True

### Reading data from databricks Filestore into dataframes

In [0]:
from functools import reduce
import pyspark.sql.functions as F
from pyspark.sql.types import StructType, ArrayType  

path = "dbfs:/FileStore/data/split_data/"

# There should be 18 files each with 300 k records. This would change if you change split value.
file_count = len(dbutils.fs.ls(path))
assert file_count == 18, "Data not found. You may want to check the path or run the notebook from start again. If you updated the split value, ignore this assertion error"

In [0]:
# https://stackoverflow.com/a/42540517 (This seems more proper way to merge the frames..)


# Currently Union fails as there seems to be difference between schemas in some instance in 9th Frame 

dataframes_map = map(lambda r: spark.read.option("inferSchema", True).json(r), [f"{path}data_PART_{num}.json" for num in range(file_count)])
union = reduce(lambda df1, df2: df1.unionByName(df2, allowMissingColumns=True), dataframes_map)
union.printSchema()

# dataframes = []
# for num in range(file_count):
#    print(f"Reading file data_PART_{num}.json into spark")
#    dataframes.append(spark.read.option("inferSchema", True).json(f"{path}data_PART_{num}.json"))

root
 |-- _id: string (nullable = true)
 |-- abstract: string (nullable = true)
 |-- authors: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- _id: string (nullable = true)
 |    |    |-- bio: string (nullable = true)
 |    |    |-- email: string (nullable = true)
 |    |    |-- gid: string (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |    |-- name_zh: string (nullable = true)
 |    |    |-- oid: string (nullable = true)
 |    |    |-- oid_zh: string (nullable = true)
 |    |    |-- orcid: string (nullable = true)
 |    |    |-- org: string (nullable = true)
 |    |    |-- org_zh: string (nullable = true)
 |    |    |-- orgid: string (nullable = true)
 |    |    |-- orgs: array (nullable = true)
 |    |    |    |-- element: string (containsNull = true)
 |    |    |-- orgs_zh: array (nullable = true)
 |    |    |    |-- element: string (containsNull = true)
 |    |    |-- sid: string (nullable = true)
 |    |    |-- position

In [0]:
parquet_path = "/tmp/out"

def buildFoSTable(dataframe):
    # pull required Fields
    fosFrame = dataframe.select(F.explode_outer("fos").alias("Field_of_Study"))

    # fosFrame.show()
    # Clean (delete dups, Fill NaN values?, ...)
    fosFrame = fosFrame.fillna("Unknown")
    fosFrame = fosFrame.distinct()
    
    # Append to Parquet file
    # fos_frame.write.mode('append').parquet("/tmp/out/field_of_study.parquet")
    fosFrame.write.mode('overwrite').parquet(f"{parquet_path}/field_of_study.parquet")
    
    # pull appeneded parquet file and get distinct records
    fosFrame = spark.read.parquet("/tmp/out/field_of_study.parquet")
    
    # Index
    df = fosFrame.distinct()
    df = df.select("*").withColumn("id", F.monotonically_increasing_id())
    # return the indexed Table
    return df.select("id", "Field_of_Study")
    

In [0]:
FoSFrame = buildFoSTable(union)
# map the relation in Fact Table
display(FoSFrame)

id Field_of_Study 0 Urban planning 1 Nash equilibrium 2 Art 3 Quasi-likelihood 4 Probabilistic automaton 5 Bruit 6 Reason maintenance 7 User requirements document 8 Karhunen–Loève theorem 9 Canny edge detector 10 Algebraic petri nets 11 Canonical form 12 Cooperative learning 13 Systems architecture 14 Transportation cost 15 Document management system 16 Biomedical information 17 Community of practice 18 Antichain 19 Rational function 20 Shared environment 21 Interferometry 22 Metal 23 Smart city 24 Logic model 25 Voting 26 Game tree 27 M-matrix 28 Idempotence 29 Video post-processing 30 Remote sensing image processing 31 Public service 32 Multiplex polymerase chain reaction 33 Ideal triangle 34 Bend radius 35 QAM 36 Intentional programming 37 Forbidden graph characterization 38 Von Neumann neighborhood 39 Mahalanobis distance 40 Bilinear transform 41 Message routing 42 Light barrier 43 System evaluation 44 Gravitational constant 45 Adhesion 46 Insulin infusion 47 Random effects model 48 Link management 49 Weighted Majority Algorithm 50 Logic level 51 Grammatical evolution 52 Student centered 53 Heapsort 54 Monomial basis 55 Trembling hand perfect equilibrium 56 Supervisory control theory 57 Cellular activity 58 Remote Database Access 59 Physical mobility 60 Truncated binary encoding 61 Equivocation 62 Digital literacy 63 Business objectives 64 Mobile network operator 65 VBScript 66 Server replication 67 Crime data 68 Model parameter 69 Formatted text 70 Fuzzy subset 71 Aerospace electronics 72 Antikythera mechanism 73 Unique factorization domain 74 Petascale computing 75 Directed evolution 76 Counterfactual thinking 77 Proper linear model 78 Flow chart 79 Functional anatomy 80 Critical question 81 Source material 82 Spike train 83 Font 84 Just-in-time compilation 85 Marketing department 86 Job market 87 Seismic microzonation 88 Computation tree logic 89 Cognitive reframing 90 Food texture 91 User journey 92 Component adaptation 93 Position (vector) 94 Customer knowledge 95 Automated mining 96 Constant curvature 97 Modulation coding 98 Palm print 99 Base code 100 Equivariant map 101 Complemented lattice 102 Boundary-value analysis 103 Security domain 104 Gratitude 105 Vernacular 106 Reflexive relation 107 Action-angle coordinates 108 Content Model 109 Discrete transition 110 Fork (file system) 111 Decision Linear assumption 112 Social work 113 Separation property 114 Thin-film transistor 115 Carrier grade 116 Many core 117 Demographic economics 118 Crisis response 119 Strategic interaction 120 Nominating committee 121 Visual short-term memory 122 Web design program 123 Bundle adjustment 124 Totative 125 Binary methods 126 Orthogonality (programming) 127 Syzygy (astronomy) 128 Computer management 129 Execution planning 130 Canonical coordinates 131 Magnetic resonance tagging 132 Sense of agency 133 Arterial input function 134 Category of relations 135 Glaciology 136 Nudge theory 137 PeptideAtlas 138 Reactor pressure vessel 139 Lipid microdomain 140 Time trends 141 Slow growth 142 Principal point 143 Single-frequency network 144 High frequency power 145 Scintillation 146 Bone tunnel 147 Discourse theory 148 Eye typing 149 Ideal number 150 Cell polarity 151 Parental education 152 Mammography screening 153 Euclidean distance transform 154 Orders of approximation 155 Media-independent handover 156 Inert 157 Resource map 158 Weight space 159 Gauge covariant derivative 160 Glucose-6-phosphate dehydrogenase 161 Spastic diplegia 162 Tactile discrimination 163 Intellectual Product 164 BeiDou Navigation Satellite System 165 Semantic dependency 166 DNS zone transfer 167 Systematic measurement 168 Hypocapnia 169 Atmospheric sounding 170 Blastula 171 Discontinuous systems 172 Matched group 173 Skid (automobile) 174 Trellis quantization 175 Integer relation algorithm 176 Self-esteem 177 Measurement study 178 Experimental phonetics 179 Nicotiana 180 Coherence resonance 181 Decorin 182 Unstructured mesh 183 Software engineering environment 184 

## PLAYGROUND/SANDBOX snippets

In [0]:
path = "dbfs:/FileStore/data/split_data/"

first_frame = spark.read.option("inferSchema", True).json(f"{path}data_PART_0.json")
display(first_frame)

_id abstract authors doi fos isbn issn issue keywords lang n_citation page_end page_start pdf references title url venue volume year 53e99784b7602d9701f3e3f5 null null null null null null null List() en 0 null null null null 3GIO. null List(null, null, null, null, null, null, null, null, null, null, null, null, 0) null 2011 53e99784b7602d9701f3e133 Drought is the first place in all the natural disasters in the world. It is especially serious in North China Plain. In this paper, different soil water content control levels at winter wheat growth stages are performed on Gucheng Ecological-Meteorological Integrated Observation Experiment Station of CAMS, China. Some canopy parameters, including growth conditions, dry weight, physiological parameters and hyperspectral reflectance, are measured from erecting stage to milk stage for winter wheat in 2009. The relationship between canopy parameters and soil relative moisture, canopy water content and water indices of winter wheat are established. The results show that some parameters, such as SPAD and dry weight of leaves, decrease with the increasing of soil relative moisture, while other parameters, including dry weight of caudexes, above ground dry weight, height, photosynthesis rate, intercellular CO 2 concentration, stomatal conductance and transpiration rate, increase corresponding to the soil relative moisture. Obvious linear relationship between stomatal conductance and transpiration rate is established with 45 samples, which R2 reaches to 0.6152. Finally, the fitting equations between canopy water content and water indices are regressed with b5, b6 and b7 of MODIS bands. The equations are best with b7 and worst with b5. So the fitting equations with b7 can be used to inverse the canopy water content of winter wheat using MODIS or other remote sensing images with similar bands range to MODIS in Hebei Province. © 2011 IEEE. List(List(53f45728dabfaec09f209538, null, null, null, Peijuan Wang, null, null, null, null, null, null, null, null, null, null), List(5601754345cedb3395e59457, null, null, null, Jiahua Zhang, null, null, null, null, null, null, null, null, null, null), List(53f38438dabfae4b34a08928, null, null, null, Donghui Xie, null, null, null, null, null, null, null, null, null, null), List(5601754345cedb3395e5945a, null, null, null, Yanyan Xu, null, null, null, null, null, null, null, null, null, null), List(53f43d25dabfaeecd6995149, null, null, null, Yun Xu, null, null, null, null, null, null, null, null, null, null)) 10.1109/IGARSS.2011.6049503 List(Agronomy, Moisture, Hydrology, Environmental science, Dry weight, Water content, Stomatal conductance, Transpiration, Irrigation, Soil water, Canopy) null List(canopy parameters, canopy spectrum, different soil water content control, winter wheat, irrigation, hydrology, radiometry, moisture, indexes, vegetation, indexation, dry weight, soil moisture, water content, indexing terms, spectrum, natural disaster) en 0 1933 1930 null null The relationship between canopy parameters and spectrum of winter wheat under different irrigations in Hebei Province. List(http://dx.doi.org/10.1109/IGARSS.2011.6049503) List(53a7297d20f7420be8bd4ae7, null, null, International Geoscience and Remote Sensing Symposium, null, null, null, IGARSS, null, null, null, null, 0) null 2011 53e99784b7602d9701f3e151 List(List(53f46797dabfaeb22f542630, null, null, null, Jairo Rocha, null, null, null, null, null, null, null, null, null, null), List(54328883dabfaeb4c6a8a699, null, null, null, Theo Pavlidis, null, null, null, null, null, null, null, null, null, null)) 10.1109/ICDAR.1993.395663 List(Intelligent character recognition, Pattern recognition, Computer science, Feature (computer vision), Document processing, Handwriting recognition, Optical character recognition, Feature extraction, Feature (machine learning), Artificial intelligence, Intelligent word recognition) List(handwriting recognition, prototypes, image segmentation, computer science, expert s

In [0]:
first_frame.printSchema()

root
 |-- _id: string (nullable = true)
 |-- abstract: string (nullable = true)
 |-- authors: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- _id: string (nullable = true)
 |    |    |-- bio: string (nullable = true)
 |    |    |-- email: string (nullable = true)
 |    |    |-- gid: string (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |    |-- name_zh: string (nullable = true)
 |    |    |-- oid: string (nullable = true)
 |    |    |-- oid_zh: string (nullable = true)
 |    |    |-- orcid: string (nullable = true)
 |    |    |-- org: string (nullable = true)
 |    |    |-- org_zh: string (nullable = true)
 |    |    |-- orgid: string (nullable = true)
 |    |    |-- orgs: array (nullable = true)
 |    |    |    |-- element: string (containsNull = true)
 |    |    |-- orgs_zh: array (nullable = true)
 |    |    |    |-- element: string (containsNull = true)
 |    |    |-- sid: string (nullable = true)
 |-- doi: string (nulla

In [0]:
authorsDF = first_frame.select(F.explode_outer("authors").alias("authors"))
authorsDF = authorsDF.selectExpr("authors._id", "authors.bio", "authors.email", "authors.gid", "authors.name", "authors.name_zh", "authors.oid", "authors.oid_zh", "authors.orcid", "authors.org", "authors.org_zh", "authors.orgid", "authors.orgs", "authors.orgs_zh", "authors.sid")

authorsDF.printSchema()

root
 |-- _id: string (nullable = true)
 |-- bio: string (nullable = true)
 |-- email: string (nullable = true)
 |-- gid: string (nullable = true)
 |-- name: string (nullable = true)
 |-- name_zh: string (nullable = true)
 |-- oid: string (nullable = true)
 |-- oid_zh: string (nullable = true)
 |-- orcid: string (nullable = true)
 |-- org: string (nullable = true)
 |-- org_zh: string (nullable = true)
 |-- orgid: string (nullable = true)
 |-- orgs: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- orgs_zh: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- sid: string (nullable = true)



In [0]:
display(authorsDF)

_id bio email gid name name_zh oid oid_zh orcid org org_zh orgid orgs orgs_zh sid null null null null null null null null null null null null null null null 53f45728dabfaec09f209538 null null null Peijuan Wang null null null null null null null null null null 5601754345cedb3395e59457 null null null Jiahua Zhang null null null null null null null null null null 53f38438dabfae4b34a08928 null null null Donghui Xie null null null null null null null null null null 5601754345cedb3395e5945a null null null Yanyan Xu null null null null null null null null null null 53f43d25dabfaeecd6995149 null null null Yun Xu null null null null null null null null null null 53f46797dabfaeb22f542630 null null null Jairo Rocha null null null null null null null null null null 54328883dabfaeb4c6a8a699 null null null Theo Pavlidis null null null null null null null null null null 53f43b03dabfaedce555bf2a null null null Min Pan null null null null null null null null null null 53f45ee9dabfaee43ecda842 null null null Chris C. N. Chu null null null null null null null null null null 53f42e8cdabfaee1c0a4274e null null null Hai Zhou null null null null null null null null null null 53f46946dabfaec09f24b4ed null null 5b86cf1ae1cd8e14a3fc787b Miguel Palma null 544bd9c245ce266baf189c4f null null Miguel Palma Studio null null null null null 53f43d95dabfaedf435b63fa null null 5b869031e1cd8e14a34a782f Maureen Squillace null null null null Fox Studios Australia, Moore Park, New South Wales, Australia null 5f71b2e41c455f439fe3efd1 null null null 54484654dabfae87b7dfc077 null null null Jon G. Hall null null null null null null null null null 433474 53f39e3edabfae4b34aa8c4a null null null Jungil Park null null null null null null null null null 237372 53f431bcdabfaee2a1cb41b5 null null null Sunyoung Ahn null null null null null null null null null 24447851 53f46ac3dabfaeee22a63eab null null null Youngmi Kim Pak null null null null null null null null null 4241287 53f44f6adabfaedf435efcb8 null null null James Jungho Pak null null null null null null null null null 22875855 53f45ad4dabfaee1c0b3e206 null null null Bonnie Mitchell null null null null null null null null null null 53f438d0dabfaeee229c1f1c null null null Naotaka Tanaka null null null null null null null null null null 53f47083dabfaeee22a79321 null null null Mio Yamamoto null null null null null null null null null null 53f4312edabfaee02ac9110a null null 5b86cf86e1cd8e14a3ff9ffc Daniel Zdunczyk null null null null Wroclaw, Poland null null null null null 560175b545cedb3395e59d80 null null null C. Evans null null null null null null null null null null 53f42d5edabfaedce54c5021 null null null S. Abu Rmeileh null null null null null null null null null null 53f42d84dabfaee1c0a355c4 null null null Damien Perritaz null null null null null null null null null 3844816 53f46fa1dabfaec09f263a80 null null null Christophe Salzmann null null null null null null null null null 2269097 541023addabfae450f4d5127 null null null Denis Gillet null null null null null null null null null 17895751 53f42b9fdabfaedf434faea8 null null null Olivier Naef null null null null null null null null null 22873952 53f454cddabfaec09f2009b7 null null null Jacques Bapst null null null null null null null null null 5217547 53f47a8ddabfaee43ed42c17 null null null Frédéric Barras null null null null null null null null null 23688121 54096818dabfae8faa68bc76 null null null Elena Mugellini null null null null null null null null null 3501899 54865672dabfae8a11fb31aa null null null Omar Abou Khaled null null null null null null null null null 101612 53f44a4adabfaedd74dfe5c0 null null 5b86ab01e1cd8e14a3fb2c33 Institute of Animation, Visual Effects and Digital Postproduction null null null null Filmakademie Baden-Württemberg, Ludwigsburg, Germany null 5f71b3e41c455f439fe46157 null null null 53f42fd0dabfaedd74d553b0 null null 5b86be9ce1cd8e14a3856487 Ichiro Iwano null null null null Iwano Design, Nagakute Aichi, Japan null 5f71b2b31c455f439fe3da0a nu

In [0]:
# https://stackoverflow.com/questions/44831789/spark-sql-nested-withcolumn/44833112#44833112
import pyspark.sql.functions as F

first_frame = first_frame.select(F.explode_outer("authors").alias("a"), "*")
authors_df = first_frame.selectExpr("a._id", "a.bio", "a.email", "a.gid", "a.name", "a.name_zh", "a.oid", "a.oid_zh", "a.orcid", "a.org", "a.org_zh", "a.orgid", "a.orgs", "a.orgs_zh", "a.sid")

display(authors_df)

_id bio email gid name name_zh oid oid_zh orcid org org_zh orgid orgs orgs_zh sid null null null null null null null null null null null null null null null 53f45728dabfaec09f209538 null null null Peijuan Wang null null null null null null null null null null 5601754345cedb3395e59457 null null null Jiahua Zhang null null null null null null null null null null 53f38438dabfae4b34a08928 null null null Donghui Xie null null null null null null null null null null 5601754345cedb3395e5945a null null null Yanyan Xu null null null null null null null null null null 53f43d25dabfaeecd6995149 null null null Yun Xu null null null null null null null null null null 53f46797dabfaeb22f542630 null null null Jairo Rocha null null null null null null null null null null 54328883dabfaeb4c6a8a699 null null null Theo Pavlidis null null null null null null null null null null 53f43b03dabfaedce555bf2a null null null Min Pan null null null null null null null null null null 53f45ee9dabfaee43ecda842 null null null Chris C. N. Chu null null null null null null null null null null 53f42e8cdabfaee1c0a4274e null null null Hai Zhou null null null null null null null null null null 53f46946dabfaec09f24b4ed null null 5b86cf1ae1cd8e14a3fc787b Miguel Palma null 544bd9c245ce266baf189c4f null null Miguel Palma Studio null null null null null 53f43d95dabfaedf435b63fa null null 5b869031e1cd8e14a34a782f Maureen Squillace null null null null Fox Studios Australia, Moore Park, New South Wales, Australia null 5f71b2e41c455f439fe3efd1 null null null 54484654dabfae87b7dfc077 null null null Jon G. Hall null null null null null null null null null 433474 53f39e3edabfae4b34aa8c4a null null null Jungil Park null null null null null null null null null 237372 53f431bcdabfaee2a1cb41b5 null null null Sunyoung Ahn null null null null null null null null null 24447851 53f46ac3dabfaeee22a63eab null null null Youngmi Kim Pak null null null null null null null null null 4241287 53f44f6adabfaedf435efcb8 null null null James Jungho Pak null null null null null null null null null 22875855 53f45ad4dabfaee1c0b3e206 null null null Bonnie Mitchell null null null null null null null null null null 53f438d0dabfaeee229c1f1c null null null Naotaka Tanaka null null null null null null null null null null 53f47083dabfaeee22a79321 null null null Mio Yamamoto null null null null null null null null null null 53f4312edabfaee02ac9110a null null 5b86cf86e1cd8e14a3ff9ffc Daniel Zdunczyk null null null null Wroclaw, Poland null null null null null 560175b545cedb3395e59d80 null null null C. Evans null null null null null null null null null null 53f42d5edabfaedce54c5021 null null null S. Abu Rmeileh null null null null null null null null null null 53f42d84dabfaee1c0a355c4 null null null Damien Perritaz null null null null null null null null null 3844816 53f46fa1dabfaec09f263a80 null null null Christophe Salzmann null null null null null null null null null 2269097 541023addabfae450f4d5127 null null null Denis Gillet null null null null null null null null null 17895751 53f42b9fdabfaedf434faea8 null null null Olivier Naef null null null null null null null null null 22873952 53f454cddabfaec09f2009b7 null null null Jacques Bapst null null null null null null null null null 5217547 53f47a8ddabfaee43ed42c17 null null null Frédéric Barras null null null null null null null null null 23688121 54096818dabfae8faa68bc76 null null null Elena Mugellini null null null null null null null null null 3501899 54865672dabfae8a11fb31aa null null null Omar Abou Khaled null null null null null null null null null 101612 53f44a4adabfaedd74dfe5c0 null null 5b86ab01e1cd8e14a3fb2c33 Institute of Animation, Visual Effects and Digital Postproduction null null null null Filmakademie Baden-Württemberg, Ludwigsburg, Germany null 5f71b3e41c455f439fe46157 null null null 53f42fd0dabfaedd74d553b0 null null 5b86be9ce1cd8e14a3856487 Ichiro Iwano null null null null Iwano Design, Nagakute Aichi, Japan null 5f71b2b31c455f439fe3da0a nu

In [0]:
display(first_frame)

a _id abstract authors doi fos isbn issn issue keywords lang n_citation page_end page_start pdf references title url venue volume year null 53e99784b7602d9701f3e3f5 null null null null null null null List() en 0 null null null null 3GIO. null List(null, null, null, null, null, null, null, null, null, null, null, null, 0) null 2011 List(53f45728dabfaec09f209538, null, null, null, Peijuan Wang, null, null, null, null, null, null, null, null, null, null) 53e99784b7602d9701f3e133 Drought is the first place in all the natural disasters in the world. It is especially serious in North China Plain. In this paper, different soil water content control levels at winter wheat growth stages are performed on Gucheng Ecological-Meteorological Integrated Observation Experiment Station of CAMS, China. Some canopy parameters, including growth conditions, dry weight, physiological parameters and hyperspectral reflectance, are measured from erecting stage to milk stage for winter wheat in 2009. The relationship between canopy parameters and soil relative moisture, canopy water content and water indices of winter wheat are established. The results show that some parameters, such as SPAD and dry weight of leaves, decrease with the increasing of soil relative moisture, while other parameters, including dry weight of caudexes, above ground dry weight, height, photosynthesis rate, intercellular CO 2 concentration, stomatal conductance and transpiration rate, increase corresponding to the soil relative moisture. Obvious linear relationship between stomatal conductance and transpiration rate is established with 45 samples, which R2 reaches to 0.6152. Finally, the fitting equations between canopy water content and water indices are regressed with b5, b6 and b7 of MODIS bands. The equations are best with b7 and worst with b5. So the fitting equations with b7 can be used to inverse the canopy water content of winter wheat using MODIS or other remote sensing images with similar bands range to MODIS in Hebei Province. © 2011 IEEE. List(List(53f45728dabfaec09f209538, null, null, null, Peijuan Wang, null, null, null, null, null, null, null, null, null, null), List(5601754345cedb3395e59457, null, null, null, Jiahua Zhang, null, null, null, null, null, null, null, null, null, null), List(53f38438dabfae4b34a08928, null, null, null, Donghui Xie, null, null, null, null, null, null, null, null, null, null), List(5601754345cedb3395e5945a, null, null, null, Yanyan Xu, null, null, null, null, null, null, null, null, null, null), List(53f43d25dabfaeecd6995149, null, null, null, Yun Xu, null, null, null, null, null, null, null, null, null, null)) 10.1109/IGARSS.2011.6049503 List(Agronomy, Moisture, Hydrology, Environmental science, Dry weight, Water content, Stomatal conductance, Transpiration, Irrigation, Soil water, Canopy) null List(canopy parameters, canopy spectrum, different soil water content control, winter wheat, irrigation, hydrology, radiometry, moisture, indexes, vegetation, indexation, dry weight, soil moisture, water content, indexing terms, spectrum, natural disaster) en 0 1933 1930 null null The relationship between canopy parameters and spectrum of winter wheat under different irrigations in Hebei Province. List(http://dx.doi.org/10.1109/IGARSS.2011.6049503) List(53a7297d20f7420be8bd4ae7, null, null, International Geoscience and Remote Sensing Symposium, null, null, null, IGARSS, null, null, null, null, 0) null 2011 List(5601754345cedb3395e59457, null, null, null, Jiahua Zhang, null, null, null, null, null, null, null, null, null, null) 53e99784b7602d9701f3e133 Drought is the first place in all the natural disasters in the world. It is especially serious in North China Plain. In this paper, different soil water content control levels at winter wheat growth stages are performed on Gucheng Ecological-Meteorological Integrated Observation Experiment Station of CAMS, China. Some canopy parameters, including growth conditions, dry weight, physiological parame

In [0]:
authors_df.printSchema()

root
 |-- _id: string (nullable = true)
 |-- bio: string (nullable = true)
 |-- email: string (nullable = true)
 |-- gid: string (nullable = true)
 |-- name: string (nullable = true)
 |-- name_zh: string (nullable = true)
 |-- oid: string (nullable = true)
 |-- oid_zh: string (nullable = true)
 |-- orcid: string (nullable = true)
 |-- org: string (nullable = true)
 |-- org_zh: string (nullable = true)
 |-- orgid: string (nullable = true)
 |-- orgs: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- orgs_zh: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- sid: string (nullable = true)



In [0]:
first_frame.printSchema()

root
 |-- Field of Study: string (nullable = true)
 |-- _id: string (nullable = true)
 |-- abstract: string (nullable = true)
 |-- authors: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- _id: string (nullable = true)
 |    |    |-- bio: string (nullable = true)
 |    |    |-- email: string (nullable = true)
 |    |    |-- gid: string (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |    |-- name_zh: string (nullable = true)
 |    |    |-- oid: string (nullable = true)
 |    |    |-- oid_zh: string (nullable = true)
 |    |    |-- orcid: string (nullable = true)
 |    |    |-- org: string (nullable = true)
 |    |    |-- org_zh: string (nullable = true)
 |    |    |-- orgid: string (nullable = true)
 |    |    |-- orgs: array (nullable = true)
 |    |    |    |-- element: string (containsNull = true)
 |    |    |-- orgs_zh: array (nullable = true)
 |    |    |    |-- element: string (containsNull = true)
 |    |    |-- sid: st

In [0]:
first_frame = first_frame.select(F.explode_outer("fos").alias("Field_of_Study"), "*")
fos_frame = first_frame.select(F.col("Field_of_Study"))

# fos_frame = first_frame.select(F.explode_outer("fos").alias("Field_of_Study"))
# fos_frame = fos_frame.select(F.col("Field_of_Study"))
display(fos_frame)

Field_of_Study null Agronomy Moisture Hydrology Environmental science Dry weight Water content Stomatal conductance Transpiration Irrigation Soil water Canopy Agronomy Moisture Hydrology Environmental science Dry weight Water content Stomatal conductance Transpiration Irrigation Soil water Canopy Agronomy Moisture Hydrology Environmental science Dry weight Water content Stomatal conductance Transpiration Irrigation Soil water Canopy Agronomy Moisture Hydrology Environmental science Dry weight Water content Stomatal conductance Transpiration Irrigation Soil water Canopy Agronomy Moisture Hydrology Environmental science Dry weight Water content Stomatal conductance Transpiration Irrigation Soil water Canopy Agronomy Moisture Hydrology Environmental science Dry weight Water content Stomatal conductance Transpiration Irrigation Soil water Canopy Agronomy Moisture Hydrology Environmental science Dry weight Water content Stomatal conductance Transpiration Irrigation Soil water Canopy Agronomy Moisture Hydrology Environmental science Dry weight Water content Stomatal conductance Transpiration Irrigation Soil water Canopy Agronomy Moisture Hydrology Environmental science Dry weight Water content Stomatal conductance Transpiration Irrigation Soil water Canopy Agronomy Moisture Hydrology Environmental science Dry weight Water content Stomatal conductance Transpiration Irrigation Soil water Canopy Agronomy Moisture Hydrology Environmental science Dry weight Water content Stomatal conductance Transpiration Irrigation Soil water Canopy Intelligent character recognition Pattern recognition Computer science Feature (computer vision) Document processing Handwriting recognition Optical character recognition Feature extraction Feature (machine learning) Artificial intelligence Intelligent word recognition Intelligent character recognition Pattern recognition Computer science Feature (computer vision) Document processing Handwriting recognition Optical character recognition Feature extraction Feature (machine learning) Artificial intelligence Intelligent word recognition Intelligent character recognition Pattern recognition Computer science Feature (computer vision) Document processing Handwriting recognition Optical character recognition Feature extraction Feature (machine learning) Artificial intelligence Intelligent word recognition Intelligent character recognition Pattern recognition Computer science Feature (computer vision) Document processing Handwriting recognition Optical character recognition Feature extraction Feature (machine learning) Artificial intelligence Intelligent word recognition Intelligent character recognition Pattern recognition Computer science Feature (computer vision) Document processing Handwriting recognition Optical character recognition Feature extraction Feature (machine learning) Artificial intelligence Intelligent word recognition Intelligent character recognition Pattern recognition Computer science Feature (computer vision) Document processing Handwriting recognition Optical character recognition Feature extraction Feature (machine learning) Artificial intelligence Intelligent word recognition Intelligent character recognition Pattern recognition Computer science Feature (computer vision) Document processing Handwriting recognition Optical character recognition Feature extraction Feature (machine learning) Artificial intelligence Intelligent word recognition Intelligent character recognition Pattern recognition Computer science Feature (computer vision) Document processing Handwriting recognition Optical character recognition Feature extraction Feature (machine learning) Artificial intelligence Intelligent word recognition Intelligent character recognition Pattern recognition Computer science Feature (computer vision) Document processing Handwriting recognition Optical character recognition Feature extraction Feature (machine learning) Artificial intelligence Intelligent word recognition Intelligent character

In [0]:
fos_frame = fos_frame.distinct()
fos_frame.write.parquet("/tmp/out/field_of_study.parquet")
# fos_frame.write.mode('append').parquet("/tmp/out/field_of_study.parquet")

In [0]:
parquet_path = "/tmp/out"

def buildFoSTable(dataframes):
    for frame in dataframes:
        # pull required Fields
        fosFrame = frame.select(F.explode_outer("fos").alias("Field_of_Study"))

        # fosFrame.show()
        # Clean (delete dups, Fill NaN values?, ...)
        fosFrame = fosFrame.fillna("Unknown")
        fosFrame = fosFrame.distinct()
        
        # Append to Parquet file
        # fos_frame.write.parquet("/tmp/out/field_of_study.parquet")
        fosFrame.write.mode('append').parquet(f"{parquet_path}/field_of_study.parquet")
    # pull appeneded parquet file and get distinct records
    fosFrame = spark.read.parquet("/tmp/out/field_of_study.parquet")
    # Index
    df = fosFrame.distinct()
    df = df.select("*").withColumn("id", F.monotonically_increasing_id())

    return df.select("id", "Field_of_Study")
    # save as table
    # map the relation in Fact Table


In [0]:
# Merging Fact Tables..

df = fos_frame.distinct()
df = df.select("*").withColumn("id", F.monotonically_increasing_id())

display(df.select("id", "Field_of_Study"))

id Field_of_Study 0 Computation 1 Statistical hypothesis testing 2 Internal model 3 Data pre-processing 4 Detailed data 5 Autonomous Navigation System 6 New business development 7 Heterogeneous wireless network 8 Test set 9 Models of neural computation 10 Interval arithmetic 11 Video on demand 12 Time control 13 Work systems 14 S transform 15 Chordal graph 16 Viral fitness 17 Amateur 18 Low-pass filter 19 Data center network architectures 20 Nested word 21 Categorial grammar 22 Physical neural network 23 Touchpad 24 Construction industry 25 Segment tree 26 Difference polynomials 27 Gate array 28 Fault free 29 Types of artificial neural networks 30 Star network 31 Communication aid 32 Entrepreneurship 33 Event calculus 34 Television interference 35 Vector quantisation 36 Sitting 37 Helium 38 Elimination method 39 Gonioscopy 40 Rare events 41 Geospatial metadata 42 Application time 43 Binary heap 44 Prolongation 45 Elementary abelian group 46 Bitonic sorting 47 Equal probability 48 Centroidal Voronoi tessellation 49 Banquet 50 Affine arithmetic 51 Revised simplex method 52 Aside 53 Crisis 54 Alice and Bob 55 Approximation property 56 Truncated mean 57 Information diagram 58 Identity function 59 Clockwork 60 Replicon 61 Lithography 62 Cryptoperiod 63 ID-based cryptography 64 Visual approach 65 Pointwise mutual information 66 Key encapsulation 67 Normal science 68 Causal relations 69 Medical robotics 70 Heaven 71 Fuzzy reasoning 72 Laser printing 73 Subtyping 74 Ramsey theory 75 Copyright Act 76 Open reading frame 77 Structured light 78 Adaptive histogram equalization 79 Statistical dispersion 80 Art gallery 81 Recurrence equations 82 BLEU 83 Modernism 84 Reflective system 85 Global coherence 86 Gradient based algorithm 87 Fuzz testing 88 Formal derivative 89 Orthogonal array testing 90 Group homomorphism 91 Split-radix FFT algorithm 92 Shibboleth 93 Inventory management 94 Reserved IP addresses 95 Cultural institution 96 Contractible space 97 Optical properties of carbon nanotubes 98 Memory dependence prediction 99 Market leader 100 Lexical representation 101 Multitenancy 102 Distributed retrieval 103 Counterintuitive 104 Fully qualified name 105 Light scattering 106 Marr–Hildreth algorithm 107 Nebula 108 Active site 109 Clinical decision making 110 Individual knowledge 111 Hamlet (place) 112 Oakley protocol 113 Data store 114 Prospection 115 Parallel imaging 116 Citation database 117 Search graph 118 Axiom of dependent choice 119 Biological test 120 Quantum information processing 121 Continued fraction 122 Kernel smoother 123 Case analysis 124 Adaptive learning environment 125 Capstone 126 Complex matrix 127 Deterministic annealing 128 Code injection 129 Interpretation (philosophy) 130 Copyright infringement 131 Chi-square test 132 Anachronism 133 Microfabrication 134 Short course 135 Barnes zeta function 136 Ceteris paribus 137 Atomism 138 Economic management 139 Cineangiography 140 Historical document 141 In shuffle 142 Carrying cost 143 Intercellular transport 144 Boot sector 145 Rate of increase 146 Perceptual similarity 147 Cellular differentiation 148 Copy number analysis 149 Submersible pump 150 Finite case 151 Deviance information criterion 152 Random set theory 153 Composite effect 154 Physiological computing 155 Mechanical vibration 156 Raman spectroscopy 157 Test sample 158 Second order equation 159 Gravity compensation 160 Secondary task 161 Autumn season 162 Neural recruitment 163 Relaxase 164 Language proficiency 165 Petroleum 166 Space form 167 Wall climbing 168 Direct democracy 169 Hydrodynamic forces 170 Mr studies 171 Argumentation semantics 172 Wheatstone bridge 173 Buffer amplifier 174 Coupling constant 175 Infectious illness 176 Revenue stream 177 Fatigue resistance 178 Visual syntax 179 General regression neural network 180 Hepatic disposition 181 Robust filtering 182 Policy making 183 Speech code theory 184 Projective reconstruction 185 Sympatric speciation 186 Out of memory 187 Structural material 188 Gua

In [0]:
first_frame.select("Field_of_Study").show()

+--------------------+
|      Field_of_Study|
+--------------------+
|                null|
|            Agronomy|
|            Moisture|
|           Hydrology|
|Environmental sci...|
|          Dry weight|
|       Water content|
|Stomatal conductance|
|       Transpiration|
|          Irrigation|
|          Soil water|
|              Canopy|
|            Agronomy|
|            Moisture|
|           Hydrology|
|Environmental sci...|
|          Dry weight|
|       Water content|
|Stomatal conductance|
|       Transpiration|
+--------------------+
only showing top 20 rows



In [0]:
display(first_frame.filter(first_frame.Field_of_Study==df.Field_of_Study))

Field_of_Study Field of Study _id abstract authors doi fos isbn issn issue keywords lang n_citation page_end page_start pdf references title url venue volume year Agronomy Agronomy 53e99784b7602d9701f3e133 Drought is the first place in all the natural disasters in the world. It is especially serious in North China Plain. In this paper, different soil water content control levels at winter wheat growth stages are performed on Gucheng Ecological-Meteorological Integrated Observation Experiment Station of CAMS, China. Some canopy parameters, including growth conditions, dry weight, physiological parameters and hyperspectral reflectance, are measured from erecting stage to milk stage for winter wheat in 2009. The relationship between canopy parameters and soil relative moisture, canopy water content and water indices of winter wheat are established. The results show that some parameters, such as SPAD and dry weight of leaves, decrease with the increasing of soil relative moisture, while other parameters, including dry weight of caudexes, above ground dry weight, height, photosynthesis rate, intercellular CO 2 concentration, stomatal conductance and transpiration rate, increase corresponding to the soil relative moisture. Obvious linear relationship between stomatal conductance and transpiration rate is established with 45 samples, which R2 reaches to 0.6152. Finally, the fitting equations between canopy water content and water indices are regressed with b5, b6 and b7 of MODIS bands. The equations are best with b7 and worst with b5. So the fitting equations with b7 can be used to inverse the canopy water content of winter wheat using MODIS or other remote sensing images with similar bands range to MODIS in Hebei Province. © 2011 IEEE. List(List(53f45728dabfaec09f209538, null, null, null, Peijuan Wang, null, null, null, null, null, null, null, null, null, null), List(5601754345cedb3395e59457, null, null, null, Jiahua Zhang, null, null, null, null, null, null, null, null, null, null), List(53f38438dabfae4b34a08928, null, null, null, Donghui Xie, null, null, null, null, null, null, null, null, null, null), List(5601754345cedb3395e5945a, null, null, null, Yanyan Xu, null, null, null, null, null, null, null, null, null, null), List(53f43d25dabfaeecd6995149, null, null, null, Yun Xu, null, null, null, null, null, null, null, null, null, null)) 10.1109/IGARSS.2011.6049503 List(Agronomy, Moisture, Hydrology, Environmental science, Dry weight, Water content, Stomatal conductance, Transpiration, Irrigation, Soil water, Canopy) null List(canopy parameters, canopy spectrum, different soil water content control, winter wheat, irrigation, hydrology, radiometry, moisture, indexes, vegetation, indexation, dry weight, soil moisture, water content, indexing terms, spectrum, natural disaster) en 0 1933 1930 null null The relationship between canopy parameters and spectrum of winter wheat under different irrigations in Hebei Province. List(http://dx.doi.org/10.1109/IGARSS.2011.6049503) List(53a7297d20f7420be8bd4ae7, null, null, International Geoscience and Remote Sensing Symposium, null, null, null, IGARSS, null, null, null, null, 0) null 2011 Moisture Agronomy 53e99784b7602d9701f3e133 Drought is the first place in all the natural disasters in the world. It is especially serious in North China Plain. In this paper, different soil water content control levels at winter wheat growth stages are performed on Gucheng Ecological-Meteorological Integrated Observation Experiment Station of CAMS, China. Some canopy parameters, including growth conditions, dry weight, physiological parameters and hyperspectral reflectance, are measured from erecting stage to milk stage for winter wheat in 2009. The relationship between canopy parameters and soil relative moisture, canopy water content and water indices of winter wheat are established. The results show that some parameters, such as SPAD and dry weight of leaves, decrease with the increasing of soil relative mois

In [0]:
# https://github.com/patelatharva/Data_Lake_with_Apache_Spark/blob/master/etl.py